# Convergent Cross Mapping (CCM) Algorithm
This notebook is an attempt at replicate the results obtained by Sugihara et. al. in his [2012 Science publication](http://science.sciencemag.org/content/338/6106/496). Subsequently, the algorithm's applicability was investigated on a linear and non-linear system where the *reversed causality* phenomena were observed.

### Note
In all cases below, the true causal structure involved is $\mathbf{X} \rightarrow \mathbf{Y}$.

# Table of Contents
- [Section 0](#Section0): Methods Definition (*Skippable*)
- [Section 1](#Section1): CCM on Predator-Prey Model
- [Section 2](#Section2): CCM on Toy Example (Linear)
- [Section 3](#Section3): CCM on Non-linear Example
- [References](#References)

<a id='Section0'></a>

***

## Section 0: Library importing, environment configurations and data importing

### Import relevant packages

In [1]:
# Importing numerical packages
import numpy as np
import pandas as pd
import math

# Plot.ly visualisations
import plotly
import plotly.plotly as py
import plotly.offline as pyo # Plot.ly visualisations
import plotly.graph_objs as go # Plot.ly visualisations

### Configure environment

In [2]:
%config InlineBackend.figure_format = 'retina'
np.set_printoptions(precision=3)

# Activate Plotly Offline for Jupyter
pyo.init_notebook_mode(connected=True)

### Define data generation functions

In [3]:
def generate_two_species(gamma_xy, gamma_yx, r_x=3.7, r_y=3.8, N=1000, randomise=False):
    '''
    Generate values for a 2-species predator-prey model.
    '''
    # Add 20 time points to N to account for burn-in
    N += 20
    
    # Initialise empty values for X and Y
    ex = {
        'X': np.zeros((N,)),
        'Y': np.zeros((N,)),
    }
    
    # Create random initial conditions for X and Y
    ex['X'][0] = np.random.uniform(0, .1)
    ex['Y'][0] = np.random.uniform(0, .1)
    
    # Calculate future values for X and Y up till N
    for k in range(N - 1):
        ex['X'][k + 1] = ex['X'][k] * (r_x - r_x * ex['X'][k] - gamma_xy * ex['Y'][k])
        ex['Y'][k + 1] = ex['Y'][k] * (r_y - r_y * ex['Y'][k] - gamma_yx * ex['X'][k])
        
    # Eliminate transient behaviour by removing initial 20 data points 
    ex['X'] = ex['X'][20:]
    ex['Y'] = ex['Y'][20:]
        
    # Return as a Pandas dataframe
    return pd.DataFrame(ex)

In [4]:
def generate_toy_data(n, delay, input_type='randomNormal'):
    '''
    Generate data for toy data.

    Input:
        n: Time-series length
        delay: Delay in terms of sampling intervals
        input_type: Behaviour of 'X' ('randomNormal', 'stepUp', 'rampUp', 'sinusoidal')

    Returns:
        A Pandas DataFrame.
    '''
    # Define an empty dict
    ex = {}
    
    # Convert n to int
    n = int(n)

    # Generate source variables
    inputs = {
        'randomNormal': np.random.normal(0, 1, size=(n,)),
        'stepUp': np.append(np.zeros((100,)), np.ones(n - 100,)),
        'rampUp': np.arange(0, 1, 1/float(n)),
        'sinusoidal': np.sin(10 * np.arange(0, 1, 1 / float(n)) * np.pi / 180)
    }
    ex['X'] = inputs[input_type]

    # Initialise dependent variables
    ex['Y'] = np.zeros((n,))
    ex['Y'][0] = 0.

    # Generate dependent variables
    for t in range(n - 1 - delay):
        ex['Y'][t + 1 + delay] = 0.7 * ex['X'][t] + 0.5 * ex['Y'][t]
        
    return pd.DataFrame(ex)

In [5]:
def generate_nonlinear_system(n):
    '''
    Generate data for non-linear system.

    Input:
        n: Time-series length

    Returns:
        A Pandas DataFrame.
    '''
    # Define an empty dict
    ex = {}
    
    # Convert n to int
    n = int(n)

    # Generate source variables
    ex['X'] = np.random.uniform(4, 5, size=(n,))

    # Initialise dependent variables
    ex['Y'] = np.zeros((n,))
    ex['Y'][0] = 0.2

    # Generate dependent variables
    for t in range(n - 1):
        ex['Y'][t + 1] = 1 - 2 * abs(0.5 - (0.8 * ex['X'][t] + 0.4 * math.sqrt(abs(ex['Y'][t]))))
        
    return pd.DataFrame(ex)

In [6]:
def generate_delayed_df(df, embed_dim, delay=1):
    '''
    Generate a delayed dataframe of `embed_dim` dimensions, each phase-shifted by `delay` delay.

    Input:
        df:         Panda dataframe
        embed_dim:  Embedding dimensions (int)
        delay:      Number of samples between each time series point (int)
        
    Returns:
        A multiLevel dataframe.
    '''
    # Obtain rows of dataframe
    N = len(df)
    
    assert embed_dim > 1
    assert delay >= 1
    
    # Define empty dataframe
    output = pd.DataFrame()
    
    # Define empty list for column headers
    column_headers = []
    
    # Create d duplicates of each time-series, and shift duplicated time-series by 'delay' sampling intervals
    for field, series in df.iteritems():
        for i in range(embed_dim):
            output = pd.concat([output, series.shift(- i * delay)], axis=1)

            # Create multiLevel header
            column_headers.append((field, str(i)))
    
    # Add column headers to dataframe
    output.columns = pd.MultiIndex.from_tuples(column_headers)
    
    # Removes rows containing NaN 
    # Reset index to start from 0
    processed_output = (output
                        .dropna()
                        .reset_index(drop=True))
        
    return processed_output

### Define CCM algorithm

In [7]:
def CCM(DF, dataCol, targetCol, k, attractor_viz=False, prediction_corr_viz=False):
    '''
    Perform convergent cross-mapping (CCM) algorithm described in paper.
    Inputs:
        DF:     A Pandas DataFrame
        data:   A string corresponding to data column in DF to perform k-NN
        target: A string corresponding to target column in DF to perform prediction
        k:      Number of nearest neighbours (scalar)
    Returns:
        predictions: Predicted values (1-D array)
        causality:   Calculated causality from correlation plot (float)
    '''
    def euclidean_dist(A, B=None):
        '''
        Calculate the euclidean distance for rows in matrix A and rows in matrix B.
        If B is None, calculates distances for rows between matrix A.
        Inputs:
            A: A matrix (a x P)
            B: A matrix (b x k x P)
        Returns:
            A distance matrix (a x b), indicating the distance of all non-i-th point to the i-th point. 
        ''' 
        # Define input matrices with expanded dimensions
        A_expanded = np.expand_dims(A, 2)
        
        # Calculate distance of each point and every other point
        if B is None:
            return np.sqrt(np.sum(np.square(A_expanded - np.transpose(A_expanded, (2, 1, 0))), axis=1))
        else:
            return np.sqrt(np.sum(np.square(np.transpose(A_expanded, (0,2,1)) - B), axis=2))
   
    def kNN(k, data):
        '''
        Return the nearest neighbours to each row in data in the form of a responsibility matrix.
        Inputs:
            k:    Number of nearest neighbours (scalar)
            data: Data to perform k-NN, a numpy array (N x P)
        Returns:
            A responsibility matrix (N x k), listing the indices of the k-nearest neighbours for each row
        '''

        def responsibilities(k, distances):
            '''
            Finds the k-nearest neighbours to each point by index.
            Inputs:
                k:         Number of nearest neighbours (scalar)
                distances: A distance matrix (N x N)
            Returns:
                A responsibility matrix (N x k), listing the indices of the k-nearest neighbours for each row
            '''
            return np.argsort(distances)[:,1:(k + 1)]

        return responsibilities(k, euclidean_dist(data))

    def predict_target(data, target, responsibilities):
        '''
        Performa a prediction of the target based on a weighting of contemporaneous neighbours of data.
        Inputs:
            data:             Data values (N x P)
            target:           Target values to perform prediction (N x P)
            responsibilities: A responsibility matrix (N x k)
        Returns:
            An array of predicted target values (N)
        '''

        def calculate_weights(data, responsibilities):
            '''
            Calculate weights based on the k-nearest neighbours
            Inputs:
                data:             Data values (N x P)
                responsibilities: A responsibility matrix (N x k)
            Returns:
                A matrix of weights (N x k)
            '''
            # Obtain shape of responsibilities
            N, k = responsibilities.shape

            # Calculate values for numerator
            for i in range(k):
                numerator = np.exp( - np.divide(euclidean_dist(data, data[responsibilities]), \
                                                euclidean_dist(data, data[responsibilities])[:,0][:, np.newaxis]))

            # Calculate denominator
            denominator = np.sum(numerator, axis=1, keepdims=True)

            # Calculate and return weights
            return np.divide(numerator, denominator)
        
        weights = calculate_weights(data, responsibilities)
        return np.sum(target[responsibilities] * np.expand_dims(weights, axis=2), axis=1)
    
    def visualise_predictions(target, predictions, dataCol, targetCol):
        '''
        Create a scatterplot visualising predictions vs. target.
        Inputs:
            target:      Target values (N x P)
            predictions: Prediction values (N x P)
        '''
        trace = go.Scattergl(
            x = target[:,-1],
            y = predictions[:,-1],
            mode = 'markers',
            hoverinfo = 'none'
        )
        
        combined_data = np.append(np.append(target, predictions), np.append(0, 1))
        
        line_trace = go.Scattergl(
            x = [np.min(combined_data), np.max(combined_data)],
            y = [np.min(combined_data), np.max(combined_data)],
            mode = 'lines',
            hoverinfo = 'none',
            line = {
                'color': '#000000',
                'dash': 'dash',
                'width': 2
            }
        )
        
        layout = go.Layout(
            title = '{0} → {1} (rho = {2})'\
                    .format(targetCol, 
                            dataCol, 
                            np.round(np.corrcoef(target[:,-1], predictions[:,-1])[0,-1], 3)),
            showlegend = False,
            height = 700,
            width = 700,
            xaxis = {'title': targetCol},
            yaxis = {'title': '{0} | M({1})'.format(targetCol, dataCol), 'scaleanchor': 'x'},
        )
        
        figure = go.Figure(data=go.Data([trace, line_trace]), layout=layout)
        pyo.iplot(figure)
        
    
    ###################
    # Function begins #
    ###################
    
    # Define `data` and `target`
    data = DF[dataCol].values
    target = DF[targetCol].values
    
    # Find indices of k-nearest neighbours
    responsibilities = kNN(k, data)
    
    # Calculate predicted target values
    predictions = predict_target(data, target, responsibilities)
    
    # Create interactive attractor animation
    if attractor_viz == True:
        visualise_attractor(responsibilities, predictions)
        
    # Create correlation plot
    if prediction_corr_viz == True:
        visualise_predictions(target, predictions, dataCol, targetCol)
        
    # Calculate causality based on correlation
    causality = np.round(np.corrcoef(target[:,-1], predictions[:,-1])[0,-1], 3)
    
    return predictions, causality

<a id='Section1'></a>

***

## Section 1: Convergent Cross Mapping (CCM) Algorithm for Detecting Causality of Non-linear Dynamical Time Series
The time series used to generate the values stem from the following 2-species predator-prey equation:

$
\begin{align}
X(t + 1) &= X(t) \left[ r_x - r_x X(t) + \gamma_{xy} Y(t) \right] \\
Y(t + 1) &= Y(t) \left[ r_y - r_y Y(t) + \gamma_{yx} X(t) \right]
\end{align}
$

The initial conditions $X(0)$ and $Y(0)$ are obtained from random uniform distribution between 0 and 1 (i.e. $U(0,1)$).

Delayed time-series $\mathbf{Y}$ and $\mathbf{X}$, each with delayed embedding dimensions and lags of $L = 2$ and $\tau = 1$ were represented using variables '`data`' and '`target`' respectively.

The regulation parameters are set to be $r_x = 3.7$ and $r_y = 3.8$. 

The example below is intended to be for a unidirectional causal system (i.e. $\mathbf{X} \rightarrow \mathbf{Y}$). As such, the coupling parameters are set such that:

$
\begin{align}
\gamma_{xy} &= 0 \\
\gamma_{yx} &= 0.32
\end{align}
$

The measure of causality can be inferred from the Pearson correlation coefficient, $\rho$, from each plot.

### Generate time-series $(N = 10,000$, $L = 2$ and $\tau = 1)$

In [8]:
# Generate DataFrame
predatorPreyDF = generate_delayed_df(generate_two_species(gamma_xy=0, gamma_yx=0.32, N=10001), embed_dim=2)

print 'Shape of DataFrame: {}'.format(predatorPreyDF.shape)
predatorPreyDF.head()

Shape of DataFrame: (10000, 4)


X                   Y          
          0         1         0         1
0  0.803880  0.583332  0.539014  0.805559
1  0.583332  0.899307  0.805559  0.444837
2  0.899307  0.335051  0.444837  0.810422
3  0.335051  0.824329  0.810422  0.496934
4  0.824329  0.535799  0.496934  0.818880

### Detect causality of $\mathbf{X} \rightarrow \mathbf{Y}$

In [9]:
CCM(predatorPreyDF,
    dataCol = 'Y',
    targetCol = 'X',
    k = 3, 
    prediction_corr_viz = True);

### Detect causality of $\mathbf{Y} \rightarrow \mathbf{X}$

In [10]:
CCM(predatorPreyDF,
    dataCol = 'X',
    targetCol = 'Y',
    k = 3, 
    prediction_corr_viz = True);

### Section Summary
As seen above, the CCM algorithm was able to detect the unidirectional causality of $\mathbf{X} \rightarrow \mathbf{Y}$, and not vice-versa. Thus, the algorithm is able to quantify the causal relationship with a calculated correlation coefficient of $\rho = 0.997$.

<a id='Section2'></a>

***

## Section 2: Toy Example
### Single-Input Single Output (SISO) first-order discrete transfer function with delay

This is a linear system that typically is used to relate inputs and outputs within chemical processes.

$ 
\begin{align} 
X(t) &\sim \mathcal{N}(0, 1) \\
Y(t + 1) &= 0.7 X(t - d) + 0.5 Y(t)
\end{align}
$

Such that:
- $Y(t = 0) = 0.0$
- $d$ is the process time delay

### Generate Linear Data

In [11]:
toyDF = generate_delayed_df(generate_toy_data(10001, delay=1, input_type='randomNormal'), embed_dim=3)

print 'Shape of DataFrame: {}'.format(toyDF.shape)
toyDF.head()

Shape of DataFrame: (9999, 6)


X                             Y                    
          0         1         2         0         1         2
0 -1.977491 -0.000283 -1.982893  0.000000  0.000000 -1.384244
1 -0.000283 -1.982893  0.928377  0.000000 -1.384244 -0.000198
2 -1.982893  0.928377  0.018057 -1.384244 -0.000198 -2.080147
3  0.928377  0.018057 -0.969909 -0.000198 -2.080147  0.649765
4  0.018057 -0.969909 -1.503241 -2.080147  0.649765 -1.027433

### Detect causality of $\mathbf{X} \rightarrow \mathbf{Y}$

In [12]:
CCM(toyDF,
    dataCol = 'Y',
    targetCol = 'X',
    k = 3, 
    prediction_corr_viz = True);

### Detect causality of $\mathbf{Y} \rightarrow \mathbf{X}$

In [13]:
CCM(toyDF,
    dataCol = 'X',
    targetCol = 'Y',
    k = 3, 
    prediction_corr_viz = True);

### Summary
Here we can see that CCM has incorrectly deduced that Y causes X ($\mathbf{Y} \rightarrow \mathbf{X}$) when the true causes network structure is in fact the opposite (i.e. $\mathbf{X} \rightarrow \mathbf{Y}$). 

<a id='Section3'></a>

***

## Section 3: Non-linear System

CCM is tested on a non-linear system described below.

$
\begin{align}
X(t) &\in [4, 5] \sim U(4, 5) \\
Y(t+1) &= 1 - 2 \ \left| \ 0.5 - \left( 0.8 X(t) + 0.4 \sqrt{\left| \ Y(t) \ \right|} \right) \ \right|
\\
\text{Such that:} \\
Y(t=0) &= 0.2
\end{align}
$

In [14]:
nonlinearDF = generate_delayed_df(generate_nonlinear_system(10001), embed_dim=2)
nonlinearDF.head()

X                   Y          
          0         1         0         1
0  4.330143  4.951257  0.200000 -5.286000
1  4.951257  4.544564 -5.286000 -7.761316
2  4.544564  4.777360 -7.761316 -7.500034
3  4.777360  4.427439 -7.500034 -7.834672
4  4.427439  4.359771 -7.834672 -7.323141

### Detect causality of $\mathbf{X} \rightarrow \mathbf{Y}$

In [15]:
CCM(nonlinearDF,
    dataCol = 'Y',
    targetCol = 'X',
    k = 3, 
    prediction_corr_viz = True);

### Detect causality of $\mathbf{Y} \rightarrow \mathbf{X}$

In [16]:
CCM(nonlinearDF,
    dataCol = 'X',
    targetCol = 'Y',
    k = 3, 
    prediction_corr_viz = True);

### Summary
Again, we see that CCM has incorrectly predicted causality to occur in the direction *opposite* to the the true causal network.

<a id='References'></a>

***

# References
G. Sugihara et al., "*Detecting Causality in Complex Ecosystems*", Science, vol. **338**, no. 6106, pp. 496-500, 2012.